# Creating Supplementary Figure 1 to Compare Imputations
The purpose of this Jupyter Notebook is to compare the raw filtered data with the imputed data from SAVER, scImpute, and MAGIC.

### Part 0: Importing Packges

In [19]:
# import statements
import magic
import scprep
import csv

import numpy as np
import pandas as pd
import matplotlib
import matplotlib.pyplot as plt
%matplotlib inline

from sklearn.decomposition import PCA
from sklearn.manifold import TSNE
from scprep.io.csv import load_csv

### Part 1: Loading in Data

In [20]:
# load raw filtered data
dat = load_csv('../../data/imputation_intermediate/filtered_data/HIV1_Bld.csv')

In [21]:
# load scimpute data (preprocessed with R script)
scimpute_dat = load_csv('../../data/imputation_intermediate/different_imputations/scimpute_hiv1.csv')
scimpute_dat = scimpute_dat.transpose()

In [22]:
# load SAVER data (preprocessed with R script)
saver_dat = load_csv('../../data/imputation_intermediate/different_imputations/saver_hiv1.csv')
saver_dat = saver_dat.transpose()

In [23]:
# compute MAGIC here, so we have magic_op to do PCA with
magic_op = magic.MAGIC()

# compute MAGIC PCA
dat_magic=magic_op.fit_transform(dat)

Calculating MAGIC...
  Running MAGIC on 1669 cells and 22935 genes.
  Calculating graph and diffusion operator...
    Calculating PCA...


/Library/Frameworks/Python.framework/Versions/3.7/lib/python3.7/site-packages/magic/magic.py:376: UserWarning: Input matrix contains unexpressed genes. Please remove them prior to running MAGIC.
  warnings.warn("Input matrix contains unexpressed genes. "


    Calculated PCA in 3.35 seconds.
    Calculating KNN search...
    Calculated KNN search in 0.37 seconds.
    Calculating affinities...
    Calculated affinities in 0.33 seconds.
  Calculated graph and diffusion operator in 4.26 seconds.
  Calculating imputation...
    Automatically selected t = 13
  Calculated imputation in 0.46 seconds.
Calculated MAGIC in 5.84 seconds.


### Part 2: PCA on Raw and Imputed Matrices

In [24]:
# confirm all four matrices are the same shape
print(dat.shape)
print(scimpute_dat.shape)
print(saver_dat.shape)
print(dat_magic.shape)

(1669, 22935)
(1669, 22935)
(1669, 22935)
(1669, 22935)


In [25]:
# compute raw PCA
dat_pca = PCA().fit_transform(np.array(dat))

In [26]:
# compute scimpute PCA
scimpute_pca = PCA().fit_transform(np.array(scimpute_dat))

In [27]:
# compute SAVER PCA
saver_pca = PCA().fit_transform(np.array(saver_dat))

In [30]:
# get color map for raw matrix
cd14_dat = dat.loc[:, 'CD14']
cd14_dat_list = np.array(cd14_dat.values.tolist())
cd14_dat_list = np.reshape(cd14_dat_list, [1669, 1])
dat_col = np.transpose(cd14_dat_list)

# get color map for scimpute matrix
cd14_scimpute = scimpute_dat.loc[:, 'CD14']
cd14_scimpute_list = np.array(cd14_scimpute.values.tolist())
cd14_scimpute_list = np.reshape(cd14_scimpute_list, [1669, 1])
scimpute_col = np.transpose(cd14_scimpute_list)

# get color map for saver matrix
cd14 = saver_dat.iloc[:,3240]

# get color map for magic matrix
cd14_magic = dat_magic.loc[:, 'CD14']
cd14_magic_list = np.array(cd14_magic.values.tolist())
cd14_magic_list = np.reshape(cd14_magic_list, [1669, 1])
magic_col = np.transpose(cd14_magic_list)

In [31]:
# plot comparison
fig, (ax1, ax2, ax3, ax4) = plt.subplots(4,1, figsize=(8, 24), dpi=800)

scprep.plot.scatter2d(dat_pca, c=dat_col, 
                      label_prefix="PC", title='PCA on Raw Data',
                      legend_title="CD14", ax=ax1, ticks=False)

scprep.plot.scatter2d(scimpute_pca, c=scimpute_col,
                      label_prefix="PC", title='PCA with scImpute',
                      legend_title="CD14", ax=ax2, ticks=False)

scprep.plot.scatter2d(saver_pca, c=cd14,
                      label_prefix="PC", title='PCA with SAVER',
                      legend_title="CD14", ax=ax3, ticks=False)

scprep.plot.scatter2d(dat_magic, c=magic_col, 
                      label_prefix="PC", title='PCA with MAGIC',
                      legend_title="CD14", ax=ax4, ticks=False)

plt.savefig('../../output/figures/supp_figure_2A_comparison_imputation_PCA.png')
plt.show()

### Part 3: t-SNE on Raw and Imputed Matrices

In [32]:
# magic t-sne
tSNE_magic=TSNE(n_components=2).fit_transform(dat_magic)

In [33]:
# raw t-sne
tSNE_dat=TSNE(n_components=2).fit_transform(dat)

In [34]:
# scimpute t-sne
tSNE_scimpute=TSNE(n_components=2).fit_transform(scimpute_dat)

In [35]:
# saver t-sne
tSNE_saver=TSNE(n_components=2).fit_transform(saver_dat)

In [36]:
# plot comparison
fig, (ax1, ax2, ax3, ax4) = plt.subplots(4,1, figsize=(8, 24), dpi=800)

scprep.plot.scatter2d(tSNE_dat, c=dat_col, 
                      label_prefix="tSNE", title='tSNE on Raw Data',
                      legend_title="CD14", ax=ax1, ticks=False)

scprep.plot.scatter2d(tSNE_scimpute, c=scimpute_col, 
                      label_prefix="tSNE", title='tSNE with scImpute',
                      legend_title="CD14", ax=ax2, ticks=False)

scprep.plot.scatter2d(tSNE_saver, c=cd14, 
                      label_prefix="tSNE", title='tSNE with SAVER',
                      legend_title="CD14", ax=ax3, ticks=False)

scprep.plot.scatter2d(tSNE_magic, c=magic_col, 
                      label_prefix="tSNE", title='tSNE with MAGIC',
                      legend_title="CD14", ax=ax4, ticks=False)

plt.savefig('../../output/figures/supp_figure_2B_comparison_imputation_tsne.png')
plt.show()